# HMC in 2D with autotuning of the mass matrix

This is a simple 2D HMC algorithm where the inverse mass matrix is approximated by BFGS updating at successive samples. No special effort is made to ensure that the mass matrix is positive definite.

**copyright**: Andreas Fichtner (andreas.fichtner@erdw.ethz.ch), December 2020

**license**: BSD 3-Clause (\"BSD New\" or \"BSD Simplified\")

## 0. Import Python packages

We begin with the import of a couple of Python packages, for plotting and for the 2D test functions that we will use.

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import test_functions as f
from importlib import reload

plt.rcParams["font.family"] = "Times"
plt.rcParams.update({'font.size': 50})
plt.rcParams['xtick.major.pad']='12'
plt.rcParams['ytick.major.pad']='12'

## 1. Input parameters

Next, we set the basic input parameters, such as the total number of samples, the number of leap-frog iterations, the leap-frog integration timestep, and the kind of probability densities, expressed in terms of their associated potential energy $U$. Currently implemented potential energies are the following:

\begin{equation}
U(x,y) = (1.0-x)^2 + 100.0 *(y-x^2)^2\,,\qquad \text{(Rosenbrock function)}\,,
\end{equation}

\begin{equation}
U(x,y) = x^2 + y^2 + xy\,,\qquad \text{(quadratic function)}\,,
\end{equation}

\begin{equation}
U(x,y) = (x^2 + y - 11.0)^2 + (x + y^2 - 7.0)^2\,,\qquad \text{(Himmelblau function)}\,,
\end{equation}

\begin{equation}
U(x,y) = (x-2.0)^4 + (x - 2.0y)^2\,,\qquad \text{(Bazaraa-Shetty function)}\,.
\end{equation}

The input parameters are defined via the custom Python function input_parameters.py in order to be able to save a set of input parameters.

In [ ]:
import input_parameters
reload(input_parameters)
function,Minv,N,Nit,dt,plot_trajectories,autotune=input_parameters.input_parameters()

## 2. Plot test function

In the next step, we visualise the potential energy surface.

In [ ]:
# Plot.
x_line=np.linspace(-2.0,2.0,100)
y_line=np.linspace(-2.0,2.0,100)
x,y=np.meshgrid(x_line,y_line)

plt.subplots(1, figsize=(30,15))
plt.pcolor(x,y,np.exp(-f.U(x,y,function)),cmap='Greys')
plt.colorbar()
plt.contour(x,y,np.exp(-f.U(x,y,function)),colors='k',alpha=0.5)
plt.xlabel('$m_1$')
plt.ylabel('$m_2$')
plt.title('potential energy',pad=20)
plt.show()

## 3. Classes for quasi-Newton autotuning 

For later convenience, we introduce classes that perform quasi-Newton updating of the inverse mass matrix, $\mathbf{M}^{-1}$. The classes perform an update of $\mathbf{M}^{-1}$ at each new sample and then compute the Cholesky decomposition of the update. The classes are written for arbitrary dimension, but it is clear that the brute-force Cholesky decomposition will only be feasible for low dimensions. $$ $$

### 3.0. No updating

In [ ]:
class no_update:
    
    def __init__(self,dim,Minv,m,g):
        """
        Initialise the no update iteration.
        
        :param dim: number of model-space dimensions
        :param Minv: initial mass matrix inverse 
        :param m: current model vector
        :param g: current gradient
        
        The matrix Minv plays the role of the inverse mass matrix, which ideally is the inverse Hessian, i.e., the covariance matrix.
        """
        
        self.dim=dim
        self.Minv=Minv
        LT=np.linalg.cholesky(self.Minv).transpose()
        self.LTinv=np.linalg.inv(LT)
        self.m=m
        self.g=g
        
    def update(self,m,g):
        """
        :param m: current model vector
        :param g: current gradient
        """
        
        

### 3.1. BFGS updating

In [ ]:
class bfgs:
    
    def __init__(self,dim,Minv,m,g):
        """
        Initialise the BFGS iteration.
        
        :param dim: number of model-space dimensions
        :param Minv: initial mass matrix inverse 
        :param m: current model vector
        :param g: current gradient
        
        The matrix Minv plays the role of the inverse mass matrix, which ideally is the inverse Hessian, i.e., the covariance matrix.
        """
        
        self.dim=dim
        self.Minv=Minv
        LT=np.linalg.cholesky(self.Minv).transpose()
        self.LTinv=np.linalg.inv(LT)
        self.m=m
        self.g=g
        
    def update(self,m,g):
        """
        Update BFGS matrix and perform Cholesky decomposition.
        
        :param m: current model vector
        :param g: current gradient
        """
        
        # Compute differences and update vectors.
        s=m-self.m
        y=g-self.g
        
        self.m=m
        self.g=g
        
        # Compute update of BFGS matrix.
        if np.dot(s,y)>0.0:
            rho=1.0/np.dot(s,y)
            I=np.identity(self.dim)
            sy=rho*np.tensordot(s,y,axes=0)
            ss=rho*np.tensordot(s,s,axes=0)
            self.Minv=np.matmul(np.matmul((I-sy),self.Minv),(I-sy.transpose()))+ss
        
        # Compute Cholesky decomposition.
        LT=np.linalg.cholesky(self.Minv).transpose()
        self.LTinv=np.linalg.inv(LT)

### 3.2. SR1 updating

In [ ]:
class sr1:
    
    def __init__(self,dim,Minv,m,g):
        """
        Initialise the SR1 iteration.
        
        :param dim: number of model-space dimensions
        :param Minv: initial mass matrix inverse 
        :param m: current model vector
        :param g: current gradient
        
        The matrix Minv plays the role of the inverse mass matrix, which ideally is the inverse Hessian, i.e., the covariance matrix.
        """
        
        self.dim=dim
        self.Minv=Minv
        LT=np.linalg.cholesky(self.Minv).transpose()
        self.LTinv=np.linalg.inv(LT)
        self.m=m
        self.g=g
        
    def update(self,m,g):
        """
        Update SR1 matrix and perform Cholesky decomposition.
        
        :param m: current model vector
        :param g: current gradient
        """
        
        # Compute differences and update vectors.
        s=m-self.m
        y=g-self.g
        
        self.m=m
        self.g=g
        
        # Compute update of SR1 matrix.
        Ay=np.dot(self.Minv,y)
        x=s-Ay
        n=np.dot(x,y)
        if np.abs(n)>0.01*np.linalg.norm(x)*np.linalg.norm(y):
            self.Minv=self.Minv+np.tensordot(x,x,axes=0)/n
                    
        # Compute Cholesky decomposition.
        LT=np.linalg.cholesky(self.Minv).transpose()
        self.LTinv=np.linalg.inv(LT)

## 4. Leapfrog integrator

For clarity, we define the leap-frog integrator as a separate function.

In [ ]:
def leapfrog(m,p,Nt,dt,Minv,plot=False):
    """ Leapfrog integration of Hamilton's equations.
    
    :param m: Initial model (position).
    :param p: Initial momentum.
    :param Nt: Number of leapfrog time steps.
    :param dt: Integration time step.
    :param Minv: Inverse mass matrix.
    :param plot: Plot trajecotry. Only do this for small number of samples.
    
    Return final model (position) and momentum.
    """
    
    # Plot potential energy in the background.
    if plot: 
        plt.subplots(1, figsize=(30,15))
        plt.pcolor(x,y,np.exp(-f.U(x,y,function)),cmap='binary')
        plt.contour(x,y,np.exp(-f.U(x,y,function)),colors='k',alpha=0.5)
        plt.plot(m[0],m[1],'bo',MarkerSize=15)
        
    J=f.J(m[0],m[1],function)
    
    for k in range(np.int(2.0*Nt*(1.0-0.5*np.random.rand()))):
        
        if plot: m_old=m.copy()
        
        p=p-0.5*dt*J
        m=m+dt*Minv.dot(p)
        J=f.J(m[0],m[1],function)
        p=p-0.5*dt*J
        
        if plot: 
            plt.plot([m_old[0],m[0]],[m_old[1],m[1]],'r')
            plt.plot(m[0],m[1],'kx')
                
    return m, p

## 5. Run HMC

We choose a random initial model and then run the standard HMC sampler.

In [ ]:
# Initialisation. =============================================================

# Initialise sample vectors and number of accepted models.
m=np.zeros((2,N))
Minv_i=np.zeros((2,2,N))
Minv_i[:,:,0]=Minv
accept=0

# Randomly chosen initial model.
m[:,0]=2.0*(np.random.rand(1,2)-0.5)

# Evaluate gradient.
g=f.J(m[0,0],m[1,0],function)

# Initialise quasi-Newton updating.
if autotune=='bfgs':
    M=bfgs(2,Minv,m[:,0],g)
elif autotune=='sr1':
    M=sr1(2,Minv,m[:,0],g)
else:
    M=no_update(2,Minv,m[:,0],g)

# Sampling. ===================================================================

for it in range(N-1):

    # Randomly choose momentum.
    p=np.random.randn(2)
    p=M.LTinv.dot(p)
    
    # Evaluate energies.
    U=f.U(m[0,it],m[1,it],function)
    K=0.5*np.dot(p,np.dot(M.Minv,p))
    H=U+K
    
    # Run leapfrog iteration.
    m_new,p_new=leapfrog(m[:,it],p,Nit,dt,M.Minv,plot=plot_trajectories)
    
    # Evaluate new energies.
    U_new=f.U(m_new[0],m_new[1],function)
    K_new=0.5*np.dot(p_new,M.Minv.dot(p_new))
    H_new=U_new+K_new
    
    # Evaluate Metropolis rule in logarithmic form.
    alpha=np.minimum(0.0,H-H_new)
    if alpha>=np.log(np.random.rand(1)):
        # Update model.
        m[:,it+1]=m_new
        accept+=1
        # Update inverse mass matrix matrix.
        g=f.J(m[0,it+1],m[1,it+1],function)
        M.update(m[:,it+1],g)
    else:
        m[:,it+1]=m[:,it]
        
    # Trace evolution of inverse mass matrix.
    Minv_i[:,:,it+1]=M.Minv
        
    # Plot Hamiltonian trajectories.
    if plot_trajectories: 
        plt.xlabel(r'$m_1$')
        plt.ylabel(r'$m_2$')
        plt.show()

## 6. Analyse results

In [ ]:
# Accepted models.
print('%i of %i proposals accepted (%0.2f percent)' % (accept,N,np.float(accept)/np.float(N)))

# Posterior histogram.
plt.subplots(1, figsize=(30,15))
plt.hist2d(m[0,:],m[1,:],cmap='binary')
plt.xlabel('$m_1$')
plt.ylabel('$m_2$')
plt.xlim([x_line[0],x_line[-1]])
plt.ylim([y_line[0],y_line[-1]])
plt.colorbar()
plt.title('posterior 2D histogram',pad=20)
plt.show()

In [ ]:
# Trace plots.
plt.subplots(1, figsize=(30,15))
plt.plot(m[0,:],'k',linewidth=4)
plt.plot(m[1,:],'r',linewidth=4)
plt.title('trace plots (black=parameter 1, red=parameter 2)',pad=20)
plt.xlabel('sample index')
plt.ylabel(r'$m_1$, $m_2$')
plt.grid()
plt.show()

# Simple statistics.
mean1=np.mean(m[0,:])
stdv1=np.std(m[0,:])
mean2=np.mean(m[1,:])
stdv2=np.std(m[1,:])
print('means: (%f,%f)' % (mean1,mean2))
print('standard deviations: (%f,%f)' % (stdv1,stdv2))

# Correlations.
cc1=np.correlate(m[0]-mean1,m[0]-mean1,'full')[N-1:2*N]
cc2=np.correlate(m[1]-mean2,m[1]-mean2,'full')[N-1:2*N]
cc1=cc1/np.max(np.abs(cc1))
cc2=cc2/np.max(np.abs(cc2))

# Find index where successive values are below zero.
N1=1
while (N1<N and (cc1[N1-1]>0 or cc1[N1]>0)): N1+=1
N2=1
while (N2<N and (cc2[N2-1]>0 or cc2[N2]>0)): N2+=1
Nmax=np.max((N1,N2))
    
plt.subplots(1, figsize=(30,15))
plt.plot(cc1[0:np.min((2*Nmax,N))],'k',linewidth=4)
plt.plot(cc2[0:np.min((2*Nmax,N))],'r',linewidth=4)
plt.title('intra-parameter correlations (black=parameter 1, red=parameter 2)',pad=20)
plt.xlabel('sample index')
plt.ylabel(r'$cc(m_1)$, $cc(m_2)$')
plt.grid()
plt.show()

# Effective sample size coefficient.
N_max=50
n_eff1=1.0/(1.0+2.0*np.sum(cc1[0:N1]))
n_eff2=1.0/(1.0+2.0*np.sum(cc2[0:N2]))
print('effective sample fractions: (%f,%f)' % (n_eff1,n_eff2))

In [ ]:
plt.subplots(1, figsize=(30,15))
plt.plot(Minv_i[0,0,:],'k',linewidth=4)
plt.plot(Minv_i[1,1,:],'r',linewidth=4)
plt.title('mass matrix elements',pad=20)
plt.xlabel('sample index')
plt.ylabel(r'$M_{inv}$')
plt.grid()
plt.show()